# Espacios de color

En este notebook aprenderás a segmentar objetos utilizando el espacio de color HSV y la librería OpenCV.

## Librerías

Para la mayor parte del trabajo que realizaremos sobre las imágenes usaremos la librería *OpenCV*, *Numpy* y *Plotly*.

### OpenCV

* Librería open source
* Proporciona las herramientas necesarias para resolver problemas de visión artificial mediante una combinación de funciones de procesamiento de imágenes de bajo nivel y algoritmos de alto nivel
* Detección de rostros, detección de peatones, entre otros
* Soporte para Java, C++, Javascript

### Numpy

* Soporte para de matrices multidimensionales

### Plotly

* Publicación de gráficos interactivos



In [ ]:
import cv2
import numpy as np
import plotly.express as px

## Lectura de imágenes y el espacio de color RGB

Ejecutamos el siguiente comando para descargar una imágen.


In [ ]:
!wget https://github.com/diplomado-ia-pucp/dava/raw/main/centro1.jpg

--2023-11-25 02:28:10--  https://github.com/diplomado-ia-pucp/dava/raw/main/centro1.jpg
Resolving github.com (github.com)... 140.82.112.4
Connecting to github.com (github.com)|140.82.112.4|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/diplomado-ia-pucp/dava/main/centro1.jpg [following]
--2023-11-25 02:28:10--  https://raw.githubusercontent.com/diplomado-ia-pucp/dava/main/centro1.jpg
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.111.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 40634 (40K) [image/jpeg]
Saving to: ‘centro1.jpg’

centro1.jpg         100%[===================>]  39.68K  --.-KB/s    in 0.01s   

2023-11-25 02:28:10 (3.83 MB/s) - ‘centro1.jpg’ saved [40634/40634]



Leemos una imagen y la mostramos.

In [ ]:
# Leer
img = cv2.imread('centro1.jpg')

# Mostrar
fig = px.imshow(img)
fig.show()

La imagen no se muestra como esperamos. Esto se debe a que *OpenCV* lee las imágenes a color en el orden BGR, es decir primero el canal azul, luego el canal  verde y finalmente el canal rojo. Cuando enviamos esta imagen a dibujar, *Plotly* cree que la imagen está en formato RGB. Para solucionar esto podemos hacer un cambio en los canales de color.

In [ ]:
# Dimensiones
print(img.shape)

(366, 550, 3)


In [ ]:
# Conversión a RGB
#img = img[:, :, [2, 1, 0]] # Forma 1
#img = img[:,:,::-1] # Forma 2
img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB) # Forma 3

fig = px.imshow(img)
fig.show()

In [ ]:
# Color RGB en el pixel y=50,x=50
print(img[50,50,:])

[183 143  56]


Por defecto las imágenes están en el espacio de color RGB. Sin embargo, al momento de procesarlas, otros espacios de color pueden ser más útiles. Por ejemplo, muchas de las técnicas clásicas de visión computacional trabajan sobre imágenes en escalas de grises.

In [ ]:
# Convertir imagen a escala de grises
#imgGray = cv2.cvtColor(img, cv2.COLOR_RGB2GRAY)

# Alternativamente, uno puede leer la imagen como escala de grises así:
imgGray = cv2.imread('centro1.jpg',0)

fig = px.imshow(imgGray, binary_string=True)
fig.show()

In [ ]:
# Dimensiones de las imágenes
print(imgGray.shape)

(366, 550)


**¿Cómo segmentar la imagen?**

## Espacio de color HSV

Ahora utilizaremos el espacio de color HSV para seleccionar los pixeles de la imagen que tienen un color específico. Primero convertimos la imagen a HSV y calculamos cuál es el color HSV que queremos seleccionar.

In [ ]:
# Creamos un pixel de color y lo convertimos a HSV
amarillo = np.uint8([[[255,255,0]]])

amarilloHSV = cv2.cvtColor(amarillo, cv2.COLOR_RGB2HSV)
print(amarilloHSV)

[[[ 30 255 255]]]


Como vemos, hemos seleccionado el color amarilo (en RGB) y lo hemos convertido a HSV. Recuerda que el primer componente es la cromaticidad (30), el segundo componente es la saturación (255) y el tercer componente es la luminosidad (255).

Si nosotros queremos seleccionar el color amarillo en la imagen, necesitamos definir el mínimo y máximo amarillo en HSV. Esto es fácil solo basta con variar primero el Hue y definir los valores correctos de saturación para permitir amarillos más claros o oscuros.

In [ ]:
# Rango de colores
lower_amarillo = np.array([20, 50, 50])
upper_amarillo = np.array([40, 255, 255])

# Convertimos la imagen de RGB a HSV
imgHSV = cv2.cvtColor(img, cv2.COLOR_RGB2HSV)

# Buscamos todos los pixeles que estan entre el minimo y maximo amarillo
mask = cv2.inRange(imgHSV, lower_amarillo, upper_amarillo)

# Obtenemos solo los pixeles que tienen las propiedades definidas
res = cv2.bitwise_and(img, img, mask = mask)

# Mostramos las imágenes
from plotly.subplots import make_subplots

fig = make_subplots(rows=1,cols=2)
fig.add_trace(px.imshow(mask,binary_string=True).data[0], 1, 1)
fig.add_trace(px.imshow(res).data[0], 1, 2)

fig.show()

In [ ]:
# Creamos una paleta de colores HSV
paleta = np.zeros((180, 50, 3), np.uint8)

for i in range(0, 180):
  for j in range(0, 50):
    paleta[i,j,0] = i # H ...
    paleta[i,j,1] = 255 # S
    paleta[i,j,2] = 255 # V

paletaRGB = cv2.cvtColor(paleta, cv2.COLOR_HSV2RGB)

fig = px.imshow(paletaRGB)
fig.show()

In [ ]:
# Paleta para un color HSV
paleta = np.zeros((255,255,3), np.uint8)

for i in range(255):
  for j in range(255):
    paleta[i,j,0] = 120
    paleta[i,j,1] = i
    paleta[i,j,2] = j

paletaRGB = cv2.cvtColor(paleta, cv2.COLOR_HSV2RGB)

fig = px.imshow(paletaRGB)
fig.show()

## Segmentación de células

En análisis de imágenes médicas, las imágenes de células sanguíneas en tejidos del estómago revelan la presencia de leucocitos atrofiados. Esta presencia indica una alta probabilidad de padecer de cáncer. Las células atrofiadas presentan un color azulado profundo que se diferencia del resto de células de la imagen. Utilizamos el análisis de espacio de colores para segmentar las células atrofiadas.

In [ ]:
!wget https://github.com/diplomado-ia-pucp/dava/raw/main/pathology_cll20x01.jpg
!wget https://github.com/diplomado-ia-pucp/dava/raw/main/pathology_cll40x03.jpg

--2023-11-25 02:58:25--  https://github.com/diplomado-ia-pucp/dava/raw/main/pathology_cll20x01.jpg
Resolving github.com (github.com)... 140.82.113.3
Connecting to github.com (github.com)|140.82.113.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/diplomado-ia-pucp/dava/main/pathology_cll20x01.jpg [following]
--2023-11-25 02:58:25--  https://raw.githubusercontent.com/diplomado-ia-pucp/dava/main/pathology_cll20x01.jpg
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.111.133, 185.199.108.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.111.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 212361 (207K) [image/jpeg]
Saving to: ‘pathology_cll20x01.jpg’

pathology_cll20x01. 100%[===================>] 207.38K  --.-KB/s    in 0.03s   

2023-11-25 02:58:26 (5.84 MB/s) - ‘pathology_cll20x01.jpg’ saved [212361/212361]

--2023-

In [ ]:
img1 = cv2.imread('pathology_cll20x01.jpg')
img2 = cv2.imread('pathology_cll40x03.jpg')

img1 = cv2.cvtColor(img1, cv2.COLOR_BGR2RGB)
img2 = cv2.cvtColor(img2, cv2.COLOR_BGR2RGB)

fig = px.imshow(img1)
fig.show()

fig = px.imshow(img2)
fig.show()

In [ ]:
# Rango de colores
lower_azul = np.array([100, 220, 0])
upper_azul = np.array([140, 255, 255])

# Convertimos la imagen de RGB a HSV
img1HSV = cv2.cvtColor(img1, cv2.COLOR_RGB2HSV)

# Buscamos todos los pixeles que estan entre el minimo y maximo amarillo
mask1 = cv2.inRange(img1HSV, lower_azul, upper_azul)

# Obtenemos solo los pixeles que tienen las propiedades definidas
res1 = cv2.bitwise_and(img1, img1, mask = mask1)

px.imshow(res1).show()

## Tarea

Realizar la segmentación de frutos rojos utilizando el espacio de color HSV



In [ ]:
!wget https://github.com/diplomado-ia-pucp/dava/raw/main/frutos_rojos.png

--2023-11-25 03:03:33--  https://github.com/diplomado-ia-pucp/dava/raw/main/frutos_rojos.png
Resolving github.com (github.com)... 140.82.113.3
Connecting to github.com (github.com)|140.82.113.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/diplomado-ia-pucp/dava/main/frutos_rojos.png [following]
--2023-11-25 03:03:34--  https://raw.githubusercontent.com/diplomado-ia-pucp/dava/main/frutos_rojos.png
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.111.133, 185.199.108.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 580583 (567K) [image/png]
Saving to: ‘frutos_rojos.png’

frutos_rojos.png    100%[===================>] 566.98K  --.-KB/s    in 0.05s   

2023-11-25 03:03:34 (10.7 MB/s) - ‘frutos_rojos.png’ saved [580583/580583]



In [ ]:
img = cv2.imread('frutos_rojos.png')
img = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)

px.imshow(img).show()